In [4]:
import streamlit as st
import pandas as pd
import plotly.express as px
import plotly.io as pio

pio.templates.default = None

from mainnet_launch.constants import AutopoolConstants, CACHE_TIME, eth_client, ROOT_PRICE_ORACLE
from mainnet_launch.constants import BAL_ETH, AUTO_ETH, AUTO_LRT
from mainnet_launch.lens_contract import get_pools_and_destinations_call, build_proxyGetDestinationSummaryStats_call
from mainnet_launch.data_fetching.get_state_by_block import get_raw_state_by_blocks, get_state_by_one_block
from mainnet_launch.destinations import DestinationDetails, get_destination_details
from mainnet_launch.data_fetching.get_state_by_block import build_blocks_to_use, safe_normalize_with_bool_success, identity_with_bool_success
from multicall import Call


def _handle_getPoolTokens(success, data):
    if success:
        tokens, balances, lastChangeBlock =data
        return {t:b/1e18 for t, b in zip(tokens, balances)}
            


def build_get_pool_tokens_call(name:str,
     pool_id: bytes,
) -> Call:
    """
    # note: if you try to make this call with a pool id that does not exist then the function call will thrown an error


    @dev Returns a Pool's registered tokens, the total balance for each, and the latest block when *any* of
    the tokens' `balances` changed.

    The order of the `tokens` array is the same order that will be used in `joinPool`, `exitPool`, as well as in all
    Pool hooks (where applicable). Calls to `registerTokens` and `deregisterTokens` may change this order.

    If a Pool only registers tokens once, and these are sorted in ascending order, they will be stored in the same
    order as passed to `registerTokens`.

    Total balances include both tokens held by the Vault and those withdrawn by the Pool's Asset Managers. These are
    the amounts used by joins, exits and swaps. For a detailed breakdown of token balances, use `getPoolTokenInfo`
    instead.

    """
    BALANCER_VAULT_ADDRESS = '0xBA12222222228d8Ba445958a75a0704d566BF2C8'


    return Call(
        BALANCER_VAULT_ADDRESS,
        ["getPoolTokens(bytes32)(address[],uint256[],uint256)", pool_id],
        [('tokens', identity_with_bool_success), ('balances', identity_with_bool_success)],
    )


def build_get_pool_id_call(name: str, contract_address: str) -> Call:
    return Call(contract_address, ["getPoolId()(bytes32)"], [(name, identity_with_bool_success)])


def build_balancer_pool_get_actual_supply(name: str, contract_address: str) -> Call:
    return Call(contract_address, ["getActualSupply()(uint256)"], [(name, safe_normalize_with_bool_success)])

from mainnet_launch.data_fetching.get_state_by_block import get_state_by_one_block
dex_pool_address = '0x88794C65550DeB6b4087B7552eCf295113794410'
pool_id_call = build_get_pool_id_call('pool_id', dex_pool_address)
pool_id = get_state_by_one_block([pool_id_call], 21041634)['pool_id']


block =21041634
total_supply_call = build_balancer_pool_get_actual_supply('lpTotalSupply', dex_pool_address)
state_call = build_get_pool_tokens_call('pxETH WETH', pool_id)
state = get_state_by_one_block([state_call, total_supply_call], 21041634)
tokens, balances, lpTotalSupply = state['tokens'], state['balances'], state['lpTotalSupply']
pool_balances = {t:int(b)/1e18 for t, b in zip(tokens,balances) if t != dex_pool_address.lower()}
underlying_eth_value = sum(([v for k, v in pool_balances.items()  ]))
pool_balances

2024-11-08 17:04:06.623 WARNING streamlit.runtime.caching.cache_data_api: No runtime found, using MemoryCacheStorageManager
2024-11-08 17:04:06.627 WARNING streamlit.runtime.caching.cache_data_api: No runtime found, using MemoryCacheStorageManager
2024-11-08 17:04:06.629 WARNING streamlit.runtime.caching.cache_data_api: No runtime found, using MemoryCacheStorageManager


{'0x04c154b66cb340f3ae24111cc767e0184ed00cc6': 5724.692343471285,
 '0xc02aaa39b223fe8d0a0e5c4f27ead9083c756cc2': 2987.320731898671}

In [ ]:
blocks =[i for i in range(20752910,  21140540, 200)] #build_blocks_to_use()[::6]


def getPriceInEth_call(name: str, token_address: str) -> Call:
    return Call(
        ROOT_PRICE_ORACLE,
        ["getPriceInEth(address)(uint256)", token_address],
        [(name, safe_normalize_with_bool_success)],
    )
    
    

pxETH_price_call = getPriceInEth_call('pxETH_safe_price', '0x04c154b66cb340f3ae24111cc767e0184ed00cc6' )
WETH_price_call = getPriceInEth_call('WETH_safe_price', '0xc02aaa39b223fe8d0a0e5c4f27ead9083c756cc2' )

calls = [pxETH_price_call, WETH_price_call, state_call, total_supply_call]
df  = get_raw_state_by_blocks(calls, blocks)

row = get_state_by_one_block(calls, blocks[-1])
row

In [ ]:
def _compute_underlying_lp_token_value(row:dict) -> float:
    tokens, balances, lpTotalSupply = row['tokens'], row['balances'], row['lpTotalSupply']
    pool_balances = {t:int(b)/1e18 for t, b in zip(tokens,balances) if t != dex_pool_address.lower()}
    underlying_eth_value = sum(([v for k, v in pool_balances.items()  ]))
    
    return underlying_eth_value / lpTotalSupply

def _compute_safe_lp_token_value(row:dict) -> float:
    
    tokens, balances, lpTotalSupply = row['tokens'], row['balances'], row['lpTotalSupply']
    
    pool_balances = {t:int(b)/1e18 for t, b in zip(tokens,balances) if t != dex_pool_address.lower()}
    
    pxETH_balance = pool_balances['0x04c154b66cb340f3ae24111cc767e0184ed00cc6']
    WETH_balance = pool_balances['0xc02aaa39b223fe8d0a0e5c4f27ead9083c756cc2']
    
    safe_eth_value = (pxETH_balance* row['pxETH_safe_price']) + (WETH_balance * row['WETH_safe_price'])
    return safe_eth_value / lpTotalSupply


def _compute_implied_safe_lp_token_value(row:dict) -> float:
    tokens, balances, lpTotalSupply = row['tokens'], row['balances'], row['lpTotalSupply']
    
    pool_balances = {t:int(b)/1e18 for t, b in zip(tokens,balances) if t != dex_pool_address.lower()}
    pxETH_balance = pool_balances['0x04c154b66cb340f3ae24111cc767e0184ed00cc6']
    WETH_balance = pool_balances['0xc02aaa39b223fe8d0a0e5c4f27ead9083c756cc2']
    
    pxETH_discount = 1 - row['pxETH_safe_price']
    weth_discount = 0
    
    safe_px_eth_value = pxETH_balance * row['pxETH_safe_price']
    safe_eth_value = WETH_balance * row['WETH_safe_price']
    
    safe_tvl = safe_px_eth_value  + safe_eth_value

    return pxETH_discount * .5


def _add_portion_px_ETH(row) -> float:
    tokens, balances, lpTotalSupply = row['tokens'], row['balances'], row['lpTotalSupply']

    pool_balances = {t:int(b)/1e18 for t, b in zip(tokens,balances) if t != dex_pool_address.lower()}
    
    pxETH_balance = pool_balances['0x04c154b66cb340f3ae24111cc767e0184ed00cc6']
    WETH_balance = pool_balances['0xc02aaa39b223fe8d0a0e5c4f27ead9083c756cc2']
    
    safe_eth_value = (pxETH_balance* row['pxETH_safe_price']) + (WETH_balance * row['WETH_safe_price'])
    return (pxETH_balance* row['pxETH_safe_price']) / safe_eth_value


def _compute_weighted_discount(row:dict):
    tokens, balances, lpTotalSupply = row['tokens'], row['balances'], row['lpTotalSupply']
    
    pool_balances = {t:int(b)/1e18 for t, b in zip(tokens,balances) if t != dex_pool_address.lower()}
    pxETH_balance = pool_balances['0x04c154b66cb340f3ae24111cc767e0184ed00cc6']
    WETH_balance = pool_balances['0xc02aaa39b223fe8d0a0e5c4f27ead9083c756cc2']
    
    pxETH_discount = 1 - row['pxETH_safe_price']
    weth_discount = 0
    
    safe_px_eth_value = pxETH_balance * row['pxETH_safe_price']
    safe_eth_value = WETH_balance * row['WETH_safe_price']
    
    safe_tvl = safe_px_eth_value  + safe_eth_value
    
    portion_pxETH = safe_px_eth_value / safe_tvl
    portion_weth = safe_eth_value / safe_tvl
    
    weighted_discount = (portion_pxETH * pxETH_discount) + (portion_weth * weth_discount) 
    return weighted_discount

df['weighted_discount'] = df.apply(_compute_weighted_discount, axis=1)
df['naive_price_return'] = (df['underlying_eth_lp_token_value'] - df['safe_eth_lp_token_value']) / df['safe_eth_lp_token_value']
df['portion_pxETH'] = df.apply(_add_portion_px_ETH, axis=1)
df['pxETH_discount'] = 1 - df['pxETH_safe_price']
df['underlying_eth_lp_token_value'] = df.apply(_compute_underlying_lp_token_value, axis=1)
df['safe_eth_lp_token_value']  = df.apply(_compute_safe_lp_token_value, axis=1)
df['price_return_if_half_assets_are_each_token'] =df.apply(_compute_implied_safe_lp_token_value, axis=1)
df
# px.line(df[['price_return_if_half_assets_are_each_token', 'naive_price_return', 'pxETH_discount']])

pxETH_safe_price  WETH_safe_price  \
timestamp                                                      
2024-09-15 02:04:47+00:00          0.998678              1.0   
2024-09-15 02:44:59+00:00          0.998678              1.0   
2024-09-15 03:25:11+00:00          0.998678              1.0   
2024-09-15 04:05:11+00:00          0.998678              1.0   
2024-09-15 04:45:35+00:00          0.998678              1.0   
...                                     ...              ...   
2024-11-08 01:41:23+00:00          0.997256              1.0   
2024-11-08 02:22:35+00:00          0.997252              1.0   
2024-11-08 03:03:11+00:00          0.997247              1.0   
2024-11-08 03:43:35+00:00          0.997243              1.0   
2024-11-08 04:23:35+00:00          0.997239              1.0   

                                                                      tokens  \
timestamp                                                                      
2024-09-15 02:04:47+00:00  (0x04c154b66cb340f3ae24111cc767e0184ed00cc6, 0...   
2024-09-15 02:44:59+00:00  (0x04c154b66cb340f3ae24111cc767e0184ed00cc6, 0...   
2024-09-15 03:25:11+00:00  (0x04c154b66cb340f3ae24111cc767e0184ed00cc6, 0...   
2024-09-15 04:05:11+00:00  (0x04c154b66cb340f3ae24111cc767e0184ed00cc6, 0...   
2024-09-15 04:45:35+00:00  (0x04c154b66cb340f3ae24111cc767e0184ed00cc6, 0...   
...                                                                      ...   
2024-11-08 01:41:23+00:00  (0x04c154b66cb340f3ae24111cc767e0184ed00cc6, 0...   
2024-11-08 02:22:35+00:00  (0x04c154b66cb340f3ae24111cc767e0184ed00cc6, 0...   
2024-11-08 03:03:11+00:00  (0x04c154b66cb340f3ae24111cc767e0184ed00cc6, 0...   
2024-11-08 03:43:35+00:00  (0x04c154b66cb340f3ae24111cc767e0184ed00cc6, 0...   
2024-11-08 04:23:35+00:00  (0x04c154b66cb340f3ae24111cc767e0184ed00cc6, 0...   

                                                                    balances  \
timestamp                                                                      
2024-09-15 02:04:47+00:00  (2373953880534993282191, 259614842926741636618...   
2024-09-15 02:44:59+00:00  (2373953880534993282191, 259614842926741636618...   
2024-09-15 03:25:11+00:00  (2373953880534993282191, 259614842926741636618...   
2024-09-15 04:05:11+00:00  (2373953880534993282191, 259614842926741636618...   
2024-09-15 04:45:35+00:00  (2373953880534993282191, 259614842926741636618...   
...                                                                      ...   
2024-11-08 01:41:23+00:00  (5239044628979658165211, 259614842926741689463...   
2024-11-08 02:22:35+00:00  (5239044628979658165211, 259614842926741689463...   
2024-11-08 03:03:11+00:00  (5239044628979658165211, 259614842926741689463...   
2024-11-08 03:43:35+00:00  (5239044628979658165211, 259614842926741689463...   
2024-11-08 04:23:35+00:00  (5239044628979658165211, 259614842926741689463...   

                           lpTotalSupply  portion_pxETH  pxETH_discount  \
timestamp                                                                 
2024-09-15 02:04:47+00:00    3626.969102       0.652546        0.001322   
2024-09-15 02:44:59+00:00    3626.969102       0.652546        0.001322   
2024-09-15 03:25:11+00:00    3626.969102       0.652546        0.001322   
2024-09-15 04:05:11+00:00    3626.969102       0.652546        0.001322   
2024-09-15 04:45:35+00:00    3626.969102       0.652546        0.001322   
...                                  ...            ...             ...   
2024-11-08 01:41:23+00:00    8031.805146       0.649921        0.002744   
2024-11-08 02:22:35+00:00    8031.805146       0.649920        0.002748   
2024-11-08 03:03:11+00:00    8031.805146       0.649919        0.002753   
2024-11-08 03:43:35+00:00    8031.805146       0.649918        0.002757   
2024-11-08 04:23:35+00:00    8031.805146       0.649918        0.002761   

                           underlying_eth_lp_token_value  \
timestamp                                                  
2024-09-15 02:04

In [128]:
px.line(df[[ 'naive_price_return', 'price_return_if_half_assets_are_each_token']])

In [126]:
px.line(df['safe_eth_lp_token_value'])

In [125]:
df.columns

Index(['pxETH_safe_price', 'WETH_safe_price', 'tokens', 'balances',
       'lpTotalSupply', 'portion_pxETH', 'pxETH_discount',
       'underlying_eth_lp_token_value', 'safe_eth_lp_token_value',
       'price_return_if_half_assets_are_each_token', 'weighted_discount',
       'naive_price_return'],
      dtype='object')

In [ ]:
curve_pool = '0xe080027Bd47353b5D1639772b4a75E9Ed3658A0d'
from multicall import Call
c =  Call(curve_pool, ["get_virtual_price()(uint256)"], [('osETH-reETH_vp', safe_normalize_with_bool_success)])
curve_df = get_raw_state_by_blocks([c], build_blocks_to_use())


2024-11-08 17:06:12.362 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-11-08 17:06:12.364 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-11-08 17:06:12.364 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-11-08 17:06:12.365 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-11-08 17:06:12.366 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.


In [12]:
px.line(365 *(curve_df.resample('1D').last().diff() / curve_df.resample('1D').last().shift(1) ))

In [14]:
int((121520311599165325472*1e18) // 1016026968466993636)

119603431179113431040

In [ ]:
 # correct amount in 119603431179113431040

In [15]:
119628263027667695059 - 119603431179113431040

24831848554264019

In [ ]:
24831848554264019 /1e18 # I think we are gettin .024 extra LP tokens here here

0.02483184855426402

In [10]:
px.line(curve_df.resample('1D').last())

In [17]:
(119628263027667695059 - 119603431179113431040) /1e18

0.02483184855426402

In [ ]:
# 13

In [123]:
.68 *20

13.600000000000001

In [124]:
# 13.600000000000001
px.line(df[['portion_pxETH']])

In [ ]:
px.line(df[[ 'pxETH_discount']])

In [ ]:
df.head()

pxETH_safe_price  WETH_safe_price  \
timestamp                                                      
2024-09-15 02:04:47+00:00          0.998678              1.0   
2024-09-16 00:03:11+00:00          0.997598              1.0   
2024-09-16 22:06:23+00:00          0.996924              1.0   
2024-09-17 20:09:47+00:00          0.998737              1.0   
2024-09-18 18:12:23+00:00          0.998868              1.0   

                                                                      tokens  \
timestamp                                                                      
2024-09-15 02:04:47+00:00  (0x04c154b66cb340f3ae24111cc767e0184ed00cc6, 0...   
2024-09-16 00:03:11+00:00  (0x04c154b66cb340f3ae24111cc767e0184ed00cc6, 0...   
2024-09-16 22:06:23+00:00  (0x04c154b66cb340f3ae24111cc767e0184ed00cc6, 0...   
2024-09-17 20:09:47+00:00  (0x04c154b66cb340f3ae24111cc767e0184ed00cc6, 0...   
2024-09-18 18:12:23+00:00  (0x04c154b66cb340f3ae24111cc767e0184ed00cc6, 0...   

                                                                    balances  \
timestamp                                                                      
2024-09-15 02:04:47+00:00  (2373953880534993282191, 259614842926741636618...   
2024-09-16 00:03:11+00:00  (2388944082788364984107, 259614842926741636618...   
2024-09-16 22:06:23+00:00  (2566129974384460040971, 259614842926741636028...   
2024-09-17 20:09:47+00:00  (2530319968046601971504, 259614842926741636028...   
2024-09-18 18:12:23+00:00  (2530319968046601971504, 259614842926741636028...   

                           lpTotalSupply  underlying_eth_lp_token_value  \
timestamp                                                                 
2024-09-15 02:04:47+00:00    3626.969102                       1.002577   
2024-09-16 00:03:11+00:00    3626.969700                       1.002583   
2024-09-16 22:06:23+00:00    4024.641179                       1.002557   
2024-09-17 20:09:47+00:00    4024.642607                       1.002546   
2024-09-18 18:12:23+00:00    4024.642607                       1.002546   

                           safe_eth_lp_token_value  naive_price_return  \
timestamp                                                                
2024-09-15 02:04:47+00:00                 1.001712            0.000863   
2024-09-16 00:03:11+00:00                 1.001001            0.001581   
2024-09-16 22:06:23+00:00                 1.000596            0.001960   
2024-09-17 20:09:47+00:00                 1.001752            0.000793   
2024-09-18 18:12:23+00:00                 1.001835            0.000710   

                           weighted_discount  implied_growth  \
timestamp                                                      
2024-09-15 02:04:47+00:00           0.000862        0.000661   
2024-09-16 00:03:11+00:00           0.001577        0.001201   
2024-09-16 22:06:23+00:00           0.001954        0.001538   
2024-09-17 20:09:47+00:00           0.000792        0.000632   
2024-09-18 18:12:23+00:00           0.000709        0.000566   

                           price_return_if_half_assets_are_each_token  \
timestamp                                                               
2024-09-15 02:04:47+00:00                                    0.000661   
2024-09-16 00:03:11+00:00                                    0.001201   
2024-09-16 22:06:23+00:00                                    0.001538   
2024-09-17 20:09:47+00:00                                    0.000632   
2024-09-18 18:12:23+00:00                                    0.000566   

                           pxETH_discount  portion_pxETH  
timestamp                                                 
2024-09-15 02:04:47+00:00        0.001322       0.652546  
2024-09-16 00:03:11+00:00        0.002402       0.656422  
2024-09-16 22:06:23+00:00        0.003076       0.635265  
2024-09-17 20:09:47+00:00        0.001263       0.626814  
2024-09-18 18:12:23+00:00        0.001132       0.626845

In [108]:
px.scatter(df, 'portion_pxETH', 'pxETH_discount', trendline='ols')

In [110]:
px.scatter(df, 'pxETH_discount', 'portion_pxETH', trendline='ols')

In [112]:
for col in df.columns:
    try:
        px.scatter(df, 'pxETH_discount', col, trendline='ols').show()
    except Exception as e:
        print(col)

/home/parker/Documents/Tokemak/v2-rebalance-dashboard/.venv/lib/python3.10/site-packages/statsmodels/regression/linear_model.py:1782: RuntimeWarning:

divide by zero encountered in scalar divide



tokens
balances


In [ ]:
px.line(df[['naive_price_return', 'weighted_discount']] * 100) # only in the 20 bips range

In [ ]:
df.columns

Index(['pxETH_safe_price', 'WETH_safe_price', 'tokens', 'balances',
       'lpTotalSupply', 'underlying_eth_lp_token_value',
       'safe_eth_lp_token_value', 'naive_price_return', 'weighted_discount'],
      dtype='object')

In [113]:
px.scatter(df, 'weighted_discount', 'safe_eth_lp_token_value', trendline='ols')

In [115]:
df.columns

Index(['pxETH_safe_price', 'WETH_safe_price', 'tokens', 'balances',
       'lpTotalSupply', 'portion_pxETH', 'pxETH_discount',
       'underlying_eth_lp_token_value', 'safe_eth_lp_token_value',
       'price_return_if_half_assets_are_each_token', 'weighted_discount',
       'naive_price_return'],
      dtype='object')

In [116]:
px.line(df[['underlying_eth_lp_token_value', 'safe_eth_lp_token_value']])

In [120]:
px.line(df[['portion_pxETH',  ]])

In [114]:
px.scatter(df, 'naive_price_return', 'safe_eth_lp_token_value', trendline='ols')

In [ ]:

prices = get_state_by_one_block([pxETH_price_call, WETH_price_call], 21041634)
prices

{'pxETH': 0.998447859558239, 'WETH': 1.0}

In [ ]:
# this pool is a pxETH/WETH pool
# the underlying value ought to be sum
# pxETH price ought to == 1





In [ ]:
#  vaultAddress	: 0x5593882d517886D190F47967168D2d68D8960F48
#  exchangeName	: balancer
#  dexPool	: 0x88794C65550DeB6b4087B7552eCf295113794410
#  lpTokenAddress	: 0x88794C65550DeB6b4087B7552eCf295113794410
#  lpTokenSymbol	: pxETH/wETH
#  lpTokenName	: Balancer pxETH/wETH StablePool
# destinations = [d for d in get_destination_details() if d.autopool.name == "balETH"]


In [ ]:
# for d in destinations:
#     if d.vault_name == 'pxETH/wETH (balancer)':
#         print(d)